In [2]:
import requests
import pandas as pd
import plotly.express as px
import folium
import plotly.io as pio

In [5]:
BASE_URL_API = "https://apidf-preprod.cerema.fr"

In [3]:
def apidf(url_endpoint, token=None):
    HEADERS = {
        "Content-Type": "application/json",
    }
    if token:
        HEADERS["Authorization"] = "Token " + token
    response = requests.get(
        url_endpoint,
        headers=HEADERS,
    )  
    if response.status_code == 200:
      return response.json()
    return None

In [42]:
# Paramétrage du endpoint
code_insee, nom = "94022", "Choisy-le-Roi"
url = BASE_URL_API + f"/indicateurs/dv3f/communes/annuel/{code_insee}"

# Interrogation de l'API et récupération d'un dataframe
response  = apidf(url)
indicateurs = pd.DataFrame.from_dict(response["results"])

# Edition du graphique
fig = px.bar(indicateurs, 
             x='annee', 
             y=['nbtrans_cod111', 'nbtrans_cod121'], 
             title = f"Evolution annuelle du nombre de ventes de logements individuels à {nom}", 
             labels={"annee" : "Année de mutation", 
                     "value" : "Nombre de ventes",},
             )
noms={"nbtrans_cod111": "Maison individuelle", 
      "nbtrans_cod121": "Appartement individuel"}
fig.update_layout(legend_title_text="Nombre de ventes")
fig.for_each_trace(lambda t: t.update(hovertemplate = t.hovertemplate.replace(t.name, noms[t.name]), name=noms[t.name]))
fig.show()

In [47]:
# Paramétrage du endpoint
code_insee, nom = "94022", "Choisy-le-Roi"
url = BASE_URL_API + f"/indicateurs/dv3f/communes/annuel/{code_insee}"

# Interrogation de l'API et récupération d'un dataframe
response  = apidf(url)
indicateurs = pd.DataFrame.from_dict(response["results"])

# Edition du graphique
fig = px.line(indicateurs, 
             x='annee', 
             y=['pxm2_median_mmx', 'pxm2_median_amx'], 
             title = f"Evolution annuelle du prix médian des logements sur {nom}", 
             range_y=[0, 5500],
             labels={"annee" : "Année de mutation", 
                     "value" : "Prix en €/m2",},
             )
noms={"pxm2_median_mmx": "Maison moyenne (entre 90 et 130 m2)", 
      "pxm2_median_amx": "Appartement ancien (T3 et T4)"}
fig.update_layout(legend_title_text="Prix médian au mètre carré")
fig.for_each_trace(lambda t: t.update(hovertemplate = t.hovertemplate.replace(t.name, noms[t.name]), name=noms[t.name]))
fig.show()

In [8]:
# Paramétrage du endpoint
code_insee, nom = "76540", "Rouen"
url = BASE_URL_API + f"/indicateurs/conso_espace/communes/{code_insee}"

# Interrogation de l'API et récupération d'un dataframe
response  = apidf(url)
indicateurs = pd.DataFrame.from_dict(response["results"])

# Edition du graphique
fig = px.bar(indicateurs, 
             x='annee', 
             y=['naf_arti', "conso_hab",  "conso_act",], 
             title = f"Evolution annuelle de la consommation d'espaces à {nom}", 
             labels={"annee" : "Année", 
                     "value" : "Surface (m2)",},
             barmode = "group",
             )
noms={"naf_arti": "totale", "conso_act": "liée à l'activité", "conso_hab": "liée à l'habitat"}
fig.update_layout(legend_title_text="Consommation d'espaces")
fig.for_each_trace(lambda t: t.update(hovertemplate = t.hovertemplate.replace(t.name, noms[t.name]), name=noms[t.name]))
fig.show()

In [40]:


# centre de la carte et 
x, y =  2.40887, 48.7625
delta_x, delta_y = 0.007, 0.007  

# définition de la bbox
x1 = x - delta_x
y1 = y - delta_y
x2 = x + delta_x
y2 = y + delta_y

# creation de la carte
m = folium.Map(location=[y, x], zoom_start=16)

url = BASE_URL_API + f"/dvf_opendata/geomutations/?in_bbox={x1},{y1},{x2},{y2}&page_size=1000"
# ajout d'une couche geojson pour chaque page de données
while True:
    response = apidf(url) 

    folium.GeoJson(response,name="mutations", popup=folium.GeoJsonPopup(fields=["libtypbien", "datemut", "valeurfonc", "sbati", "sterr"]),).add_to(m)
    if not response["next"]:
        break

    url = response["next"]

In [41]:
m

In [15]:
# Paramétrage du endpoint
code_insee, nom = "94022", "Choisy-le-Roi"
url = BASE_URL_API + f"/dvf_opendata/mutations/?code_insee={code_insee}&page_size=1000&anneemut_min=2018&codtypbien=111"

# Interrogation de l'API pour récupérer les pages de mutations
pages = []

while True:
    response = apidf(url) 
    mutations = pd.DataFrame.from_dict(response["results"])
    pages.append(mutations)
    if not response["next"]:
      break
    url = response["next"]

# concaténation des pages et affichage graphique
mutations = pd.concat(pages)
mutations["valeurfonc"] = mutations["valeurfonc"].astype(float)
fig = px.violin(mutations, 
                y="valeurfonc", 
                x="anneemut", 
                color="anneemut", 
                box=True, 
                title = f"Distribution annuelle des prix des ventes de maison à partir de 2018 à {nom}", 
                labels={"annee" : "Année", 
                        "valeurfonc" : "Prix en €",},)
fig.update_layout(legend_title_text="Année de mutation")
fig.show()

In [14]:
import geopandas as gpd
import pandas as pd
import ssl

ssl._create_default_https_context = ssl._create_unverified_context
x,y = 2.40887, 48.7625
i = 1
fdf= pd.DataFrame()

while True:
    map_adds = gpd.read_file(f"https://apidf-preprod.cerema.fr/dvf_opendata/geomutations/?in_bbox={x - 0.007},{y - 0.007},{x + 0.007},{y + 0.007}&page={i}&page_size=10000")
    fdf = pd.concat([fdf, map_adds])
    print(map_adds.shape[0])
    i += 1
    if map_adds.shape[0] < 500:
        break

print(fdf.shape[0])

500
500
500
500
500
500
500
38
3538


In [15]:
fdf.head()

idmutinvar                        idopendata  \
0  558808a02bd71ab899a2702e918289dc  558808a02bd71ab899a2702e918289dc   
1  a2ac720bd681cdacfb2865836fc24423  a2ac720bd681cdacfb2865836fc24423   
2  0a8cce0be151d52478e15f80893948bb  0a8cce0be151d52478e15f80893948bb   
3  0771bea916c0152896cd0c9c18f5eb97  0771bea916c0152896cd0c9c18f5eb97   
4  c16572488bfe4d13985b0d28191da690  c16572488bfe4d13985b0d28191da690   

      datemut  anneemut coddep libnatmut   vefa valeurfonc  nbcomm l_codinsee  \
0  2023-04-28      2023     94     Vente  False  115320.00       1    [94022]   
1  2023-05-05      2023     94     Vente  False  365000.00       1    [94022]   
2  2023-06-15      2023     94     Vente  False  160000.00       1    [94022]   
3  2023-06-09      2023     94     Vente  False  280000.00       1    [94022]   
4  2023-01-26      2023     94     Vente  False  407000.00       1    [94022]   

   ...  nbparmut l_idparmut  sterr nbvolmut nblocmut  \
0  ...         0       None   0.00        0        1   
1  ...         0       None   0.00        0        4   
2  ...         0       None   0.00        0        3   
3  ...         0       None   0.00        0        4   
4  ...         0       None   0.00        0        6   

                                          l_idlocmut   sbati codtypbien  \
0                                [940220020465514_0]   35.00        121   
1  [940220020465367_0, 940220020465368_0, 9402200...   81.00        121   
2  [940220020470383_0, 940220020470384_0, 9402200...   66.00        121   
3  [940220020470605_0, 940220020470606_0, 9402200...   73.00        121   
4  [940220020457392_0, 940220020457393_0, 9402200...  135.00        122   

          libtypbien                                           geometry  
0     UN APPARTEMENT  MULTIPOLYGON (((2.41269 48.76055, 2.41267 48.7...  
1     UN APPARTEMENT  MULTIPOLYGON (((2.41417 48.76178, 2.41417 48.7...  
2     UN APPARTEMENT  MULTIPOLYGON (((2.41006 48.76409, 2.40983 48.7...  
3     UN APPARTEMENT  MULTIPOLYGON (((2.41522 48.76482, 2.41541 48.7...  
4  DEUX APPARTEMENTS  MULTIPOLYGON (((2.40531 48.76310, 2.40538 48.7...  

[5 rows x 22 columns]

In [17]:
subs = fdf[fdf['l_codinsee'].str.contains(f'{94022}', regex=False)]

In [18]:
subs.shape[0]

3127